In [45]:
# Utilities
import re
import os
# Preprocessing
from html import unescape
from fuzzywuzzy import fuzz
# Data management
import numpy as np
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt

In [2]:
df = pd.read_csv("./data/book.txt", 
                   sep='\t', 
                   lineterminator='\n', 
                   header=None, 
                   names=["source", "isbn", "title", "authors"])

In [3]:
df.head()

source        isbn  \
0      eCampus.com  0201853949   
1        Indoo.com  0201853949   
2  textbookxdotcom  0201853949   
3          A1Books  0201853949   
4     textbooksNow  0201853949   

                                               title             authors  
0  The art Of Computer Programming, Fascicle 3: G...     Not Available\r  
1  Art of Computer Programming, Volume 4, Fascicl...  Knuth, Donald E.\r  
2  The 'art Of Computer Programming, Fascicle 3 G...                  \r  
3  The Art of Computer Programming, Volume 4, Fas...  Knuth, Donald E.\r  
4                        Art of Computer Programming             Knuth\r

In [4]:
df.describe()

source        isbn                       title authors
count     33971       33971                       33968   33971
unique      895        1265                       11095    9627
top     A1Books  0321263588  Modern Database Management      \r
freq       2403         159                          90     713

# Preprocessing

In [10]:
def clean(df, gs=False):
    if gs:
        df["authors"] = df["authors"].str.lower()
        df["authors"] = df["authors"].str.replace('[^\w\s]|\\r','')
        df.authors = df.authors.replace('\s+', ' ', regex=True)
        df.authors = df.authors.replace(r'\b\w\b', ' ', regex=True)
    else:
        # Unescape HTML left over from scraping
        df.authors = df.authors.apply(unescape)
        df.title = df.title.apply(lambda x: unescape(str(x)))
        # Lowercase 
        df["authors"] = df["authors"].str.lower()
        df["title"] = df["title"].str.lower()
        df["source"] = df["source"].str.lower()
        # Removes parenthesis from author list
        df["authors"] = df["authors"].str.replace('\((.*?)\)','')
        # Replaces | in author list with spaces
        df["authors"] = df["authors"].str.replace('\|',' ')
        # Special characters removal (removes all special characters left)
        df["title"] = df["title"].str.replace('[^\w\s]|\\r','')
        df["authors"] = df["authors"].str.replace('[^\w\s]|\\r','')
        # Uniformize missing values
        df["authors"] = df["authors"].str.replace('not available','')
        df["authors"] = df["authors"].replace(r'^\s*$', np.nan, regex=True)
        # Remove doubled whitespaces
        df.authors = df.authors.replace('\s+', ' ', regex=True)
        df.title = df.title.replace('\s+', ' ', regex=True)
        # Remove single characters in authors names
        df.authors = df.authors.replace(r'\b\w\b', ' ', regex=True)

In [11]:
clean(df)

In [14]:
df.describe()

source        isbn                                 title  \
count     33971       33971                                 33971   
unique      894        1265                                  7195   
top     a1books  0321263588  computer networking and the internet   
freq       2403         159                                   108   

               authors  
count            33227  
unique            7222  
top     knuth donald    
freq               133

In [24]:
sum(df.duplicated())

7508

In [33]:
df = df.drop_duplicates()

# Data Quality Metrics

### Completeness
Attribute/Table completeness

NOTE: Closed World assumption

In [35]:
# Null values
null_count = df.isnull().sum()
print(null_count)

source       0
isbn         0
title        0
authors    602
dtype: int64


In [36]:
# Attribute completeness
rows = df.shape[0]
attributes = list(df)
attribute_compl = {}

for attribute in attributes:
    attribute_compl[attribute] = 1 - (null_count[attribute] / rows)

attribute_compl

{'source': 1.0, 'isbn': 1.0, 'title': 1.0, 'authors': 0.9772512564712995}

In [37]:
# Table completeness
table_compl = 1 - (null_count.sum() / (len(attributes)*rows))
print(table_compl)

0.9943128141178249


### Accuracy
For each source, matching of ISBN and authors list to Golden Standard

In [38]:
gs = pd.read_csv("./data/book_golden.txt", 
                   sep='\t', 
                   lineterminator='\n', 
                   header=None, 
                   names=["isbn", "authors"])
clean(gs, gs=True)
gs

isbn                                            authors
0   9780073516677                   oleary timothy   oleary linda   
1   9780072999389                         yacht carol crosson susan 
2   9780072922363                                    hutton david   
3   9780072843996  haag stephen perry james   sosinsky barrie est...
4   9780072466850                                         reddy     
..            ...                                                ...
95     0122290631                                    eberly david   
96     0120887975                                         celko joe 
97     0120455994                         aiken peter allen   david 
98     1555581994                                     cheek matthew 
99     1555582745                       moore martin hancock steven 

[100 rows x 2 columns]

In [39]:
def compute_accuracy(source, gs):
    # Computes source accuracy by matching the golden standard rows to the source df, 
    # computing ISBN and Authors accuracy
        
    isbn_match_count = 0
    authors_match_count = 0
    authors_match_percentage = 0
    
    for gs_isbn, gs_authors in zip(gs.isbn, gs.authors):
        select = source[source.isbn == gs_isbn]
        select = select.dropna()
        if not select.empty:
            isbn_match_count += 1
            for authors in select.authors:
                tokens = authors.split()
                gs_tokens = gs_authors.split()
                match = fuzz.token_sort_ratio(tokens, gs_tokens)
                authors_match_percentage += match
                authors_match_count += 1
                
    acc = {
        "isbn": isbn_match_count/len(source.isbn),
        "authors": authors_match_percentage/authors_match_count
    }
    
    return acc

In [13]:
# Unique sources
sources = df.source.unique()

source_accuracy = []

if not os.path.exists("./data/source_accuracy.csv"):
    for source in sources:
        selected_source = df[df.source == source]
        acc = compute_accuracy(df, gs)
        acc["source"] = source
        source_accuracy.append(acc)
    
    with open('data/source_accuracy.csv', 'w') as f:
        f.write("{}, {}, {}".format("source", "isbn coverage", "authors accuracy"))
        for e in source_accuracy:
            f.write("{}, {}, {}".format(e["source"], e["isbn"], e["authors"]))

### Coverage
How much data of the dataset each source covers

In [15]:
source_coverage = {}
unique_isbn = len(df.isbn.unique())

for source in sources:
    selected_source = df[df.source == source]
    source_coverage[source] = len(selected_source.isbn.unique()) / unique_isbn

print(unique_isbn)
print(source_coverage)

1265
{'ecampus.com': 0.23873517786561266, 'indoo.com': 0.5154150197628459, 'textbookxdotcom': 0.6, 'a1books': 0.8656126482213439, 'textbooksnow': 0.2656126482213439, 'paperbackworld.de': 0.4608695652173913, 'caiman': 0.8102766798418972, 'movies with a smile': 0.108300395256917, 'marando.de versandbuchhandlung': 0.15889328063241107, 'aha-buch': 0.2458498023715415, 'versandantiquariat robert a. mueller': 0.32885375494071145, 'morgenstundt buch & kunst': 0.2276679841897233, 'alphacraze.com': 0.1241106719367589, 'odeon books': 0.1541501976284585, "powell's  books": 0.4324110671936759, 'quartermelon': 0.5154150197628459, 'browns books': 0.27509881422924903, 'books down under': 0.36996047430830037, 'swoop': 0.07509881422924901, 'thebookcom': 0.3739130434782609, 'thesaintbookstore': 0.25375494071146243, "mellon's books": 0.21818181818181817, 'blackwell online': 0.3264822134387352, 'stratford books': 0.4276679841897233, 'the book depository': 0.36363636363636365, 'englishbookservice.com gti gm

# Data Fusion

## TruthFinder implementation

In [53]:
df["trustworthiness"] = 0.9
df["fact_confidence"] = 0

In [69]:
for obj in df["isbn"].unique():
    idx = df["isbn"] == obj
    data = df[idx]
    print(data)

                                     source        isbn  \
0                               ecampus.com  0201853949   
1                                 indoo.com  0201853949   
2                           textbookxdotcom  0201853949   
3                                   a1books  0201853949   
4                              textbooksnow  0201853949   
5                         paperbackworld.de  0201853949   
6                                    caiman  0201853949   
7                       movies with a smile  0201853949   
8            marando.de versandbuchhandlung  0201853949   
9                                  aha-buch  0201853949   
10     versandantiquariat robert a. mueller  0201853949   
11                morgenstundt buch & kunst  0201853949   
12                           alphacraze.com  0201853949   
13                              odeon books  0201853949   
14                          powell's  books  0201853949   
15                             quartermelon  0201853949 

                               source        isbn  \
1132                brandnewtextbooks  0321197860   
1134               textbooks for less  0321197860   
1135                           htbook  0321197860   
1138             california textbooks  0321197860   
1139                      sandy chong  0321197860   
1140                       alinonline  0321197860   
1142                  bookworms, inc.  0321197860   
1143           collegebooksdirect.com  0321197860   
1144                     textbooksnow  0321197860   
1147                        indoo.com  0321197860   
1148                          a1books  0321197860   
1149                  textbookxdotcom  0321197860   
1150                           caiman  0321197860   
1151                       bobs books  0321197860   
1152                       dvd legacy  0321197860   
1153                    players quest  0321197860   
1155                       bobs books  0321197860   
1156                thesaintbookstore  0321197

                                    source        isbn  \
2921                    best bargain books  0201657961   
2922                             owlsbooks  0201657961   
2923               nationwide book traders  0201657961   
2924               nationwide book traders  0201657961   
2925          bookbyte / norwest textbooks  0201657961   
2926                  college book service  0201657961   
2927                      bunches of books  0201657961   
2928                           ecampus.com  0201657961   
2929                   price cut books ltd  0201657961   
2931                        monarchy books  0201657961   
2932                               a1books  0201657961   
2933                       textbookxdotcom  0201657961   
2934                mediasell (g.i.v. mbh)  0201657961   
2935                     paperbackworld.de  0201657961   
2936  versandantiquariat robert a. mueller  0201657961   
2937             morgenstundt buch & kunst  0201657961   
2938          

                            source        isbn  \
4231                   lucky books  0201710145   
4232                brian t stoval  0201710145   
4233            best bargain books  0201710145   
4234  bookbyte / norwest textbooks  0201710145   
4237              bunches of books  0201710145   
4238               oak creek books  0201710145   
4239             blumenkraft books  0201710145   
4240                   tranceworks  0201710145   
4241                  samkat books  0201710145   
4242                   ecampus.com  0201710145   
4243                     indoo.com  0201710145   
4246               textbookxdotcom  0201710145   
4247                bookmantra.com  0201710145   
4249                opoe-abe books  0201710145   
4250                       a1books  0201710145   
4252                  gunars store  0201710145   
4253                 gunter koppon  0201710145   
4254            limelight bookshop  0201710145   

                                              tit

                    source        isbn  \
5549           louis morin  0201548879   
5550          textbooksnow  0201548879   
5551        bookmantra.com  0201548879   
5552  www.textbooksrus.com  0201548879   
5553             indoo.com  0201548879   
5554       textbookxdotcom  0201548879   
5555         papamedia.com  0201548879   
5556     revaluation books  0201548879   

                                                 title  \
5549  osp an environment for operating system projects   
5550             osp environment for operating systems   
5551  osp an environment for operating system projects   
5552  osp an environment for operating system projects   
5553  osp an environment for operating system projects   
5554  osp an environment for operating system projects   
5555  osp an environment for operating system projects   
5556  osp an environment for operating system projects   

                           authors  trustworthiness  fact_confidence  
5549  kifer michael smolka 

...

                                     source        isbn  \
22523                               a1books  0120884828   
22525                                caiman  0120884828   
22526                      paperbackshop-us  0120884828   
22527                    books2anywhere.com  0120884828   
22528                       powell's  books  0120884828   
22529                       powell's  books  0120884828   
22530                      blackwell online  0120884828   
22531                          quartermelon  0120884828   
22532                          browns books  0120884828   
22533                          quartermelon  0120884828   
22534                        lakeside books  0120884828   
22536  versandantiquariat robert a. mueller  0120884828   
22537                     paperbackworld.de  0120884828   
22538                   the book depository  0120884828   
22540                            bobs books  0120884828   
22541                      books down under  0120884828 

                                source        isbn  \
23625                the bookman, inc.  155860779X   
23626                          a1books  155860779X   
23627        silicon valley fine books  155860779X   
23629        dotcom liquidators / dc 1  155860779X   
23630  vielbuch.de - onlineantiquariat  155860779X   
23631                      boox2relyon  155860779X   
23632             sarl culture-factory  155860779X   
23633              the book depository  155860779X   
23634                paperbackworld.de  155860779X   
23635                    papamedia.com  155860779X   
23636                revaluation books  155860779X   

                                                   title  \
23625  developing ipbased services solutions for serv...   
23626  developing ipbased services solutions for serv...   
23627  developing ipbased services solutions for serv...   
23629  developing ipbased services solutions for serv...   
23630  developing ip based services hardcover by mo

                                     source        isbn  \
24869                             livrenoir  1558604820   
24870                        bookmantra.com  1558604820   
24871                                caiman  1558604820   
24872                               a1books  1558604820   
24874                       book lovers usa  1558604820   
24876                       annex books inc  1558604820   
24877                    cobu gmbh & co. kg  1558604820   
24878                         papamedia.com  1558604820   
24879                              aha-buch  1558604820   
24880  versandantiquariat robert a. mueller  1558604820   
24881                     paperbackworld.de  1558604820   
24882                     revaluation books  1558604820   
24883                    limelight bookshop  1558604820   

                                                   title              authors  \
24869  a complete guide to db2 universal database ibm...    chamberlin donald   
24870  a co

                                     source        isbn  \
25659                      mega media depot  0125184069   
25660                               a1books  0125184069   
25661                   movies with a smile  0125184069   
25662                                caiman  0125184069   
25664                        bookmantra.com  0125184069   
25665                        alphacraze.com  0125184069   
25668                          quartermelon  0125184069   
25669                          browns books  0125184069   
25671                  college book service  0125184069   
25672                       book lovers usa  0125184069   
25673           the critical eye used books  0125184069   
25674                     henry's biz books  0125184069   
25675                       annex books inc  0125184069   
25676                       stratford books  0125184069   
25677                          quartermelon  0125184069   
25678                          quartermelon  0125184069 

KeyboardInterrupt: 